In [ ]:
import analytics.tranche_basket as bkt
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from analytics.scenarios import run_tranche_scenarios, run_portfolio_scenarios, run_tranche_scenarios_rolldown
from analytics import DualCorrTranche, TrancheBasket, ManualTrancheBasket
from utils.db import dbconn
from datetime import date

In [ ]:
def build_tranche_quotes(index_type, ref, quotes):
    if index_type == 'HY':
        detach = [15, 25, 35, 100] 
    elif index_type == 'IG':
        detach = [3, 7, 15, 100] 
    elif index_type == 'EU':
        detach = [3, 6, 12, 100] 
    else:
        detach = [10, 20, 35, 100]
    coupon = 500 if (index_type == 'HY' or index_type == 'XO') else 100
    if index_type == 'HY':
        ref_type1 = 'indexrefprice'
        ref_type2 = 'indexrefspread'
        ref_2 = None
    else:
        ref_type1 = 'indexrefspread'
        ref_type2 = 'indexrefprice'
        ref_2 = None
    return pd.DataFrame({"detach": np.array(detach), 
                         "trancheupfrontmid": np.array(quotes), 
                         "trancherunningmid": np.full(4, coupon),
                          ref_type1: np.full(4, ref),
                          ref_type2: np.full(4, ref_2)})

In [ ]:
index_type = 'HY'
series = 35
value_date = date.today()
df = build_tranche_quotes(index_type, 104.625, [43, 92.5, 110, 120.27])
new_index = ManualTrancheBasket(index_type, series, "5yr", value_date=value_date, tranche_quotes=df)
new_index.tweak()
new_index.build_skew()
result = pd.concat([pd.DataFrame(new_index.rho[0:4], index=new_index.tranche_thetas().index, columns=['att_corr']),
           pd.DataFrame(new_index.tranche_pvs().bond_price, index=new_index.tranche_thetas().index, columns=['price']),
           new_index.tranche_deltas(),
           new_index.tranche_thetas()],
           axis=1)
result['net_theta'] = result.theta - new_index.theta()[0] * result.delta
result

In [ ]:
#Implied SS
implied_ss = ((new_index.index_pv().bond_price - new_index.accrued()) -
              ((new_index.K[1]-new_index.K[0]) * result.price[0] +
              (new_index.K[2]-new_index.K[1]) * result.price[1] +
              (new_index.K[3]-new_index.K[2]) * result.price[2]))/(new_index.K[4] - new_index.K[3])
implied_ss

In [ ]:
#Build previous series skew to price this new series
base_index = TrancheBasket(index_type, series-2, "5yr")
base_index.tweak()
base_index.build_skew()

new_index.rho = base_index.map_skew(new_index)
result = pd.concat([pd.DataFrame(new_index.rho[0:4], index=new_index.tranche_thetas().index, columns=['att_corr']),
           pd.DataFrame(new_index.tranche_pvs().bond_price, index=new_index.tranche_thetas().index, columns=['price']),
           new_index.tranche_deltas(),
           new_index.tranche_thetas()],
           axis=1)
result['net_theta'] = result.theta - new_index.theta()[0] * result.delta
result